In [4]:
import pandas as pd
import scipy.io as sio
import numpy as np
import datetime
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import re

def Array_To_DataFrame(matDF, varName) :
    npArray = np.array([])
    for i in range (matDF[varName].shape[0]) :
        npArray = np.concatenate((npArray, matDF[varName][i].flatten()))
    return npArray


#read in surface data from each of the locations
downDF = pd.read_csv('downriver_2013_2014_processed.csv', parse_dates = ['DN'])
upDF = pd.read_csv('upriver_2013_2014_processed.csv', parse_dates = ['DN'])
midDF = pd.read_csv('midestuary_2013_2014_processed.csv', parse_dates = ['DN'])
combinedDF = pd.read_csv('ocean_temperature13_14.csv', parse_dates = ['DN', 'dayDN'])
riverCombinedDF = pd.read_csv('river_temperature13_14.csv', parse_dates = ['DN', 'dayDN'])

'''
preTimestamp = pd.Timestamp('2013-10-24 22:05:00')
postTimestamp = pd.Timestamp('2014-03-12 19:30:00') + datetime.timedelta(minutes = 5)
firstMidMark = downDF['DN'][0]
lastMidMark = downDF['DN'][len(downDF['DN'])-1] + datetime.timedelta(minutes = 5)
preTms = np.arange(preTimestamp, firstMidMark, datetime.timedelta(minutes = 5)).astype('datetime64')
refillDF = pd.DataFrame({'DN' : preTms, 'SurfaceSalCorrected' : np.repeat(np.nan, len(preTms)), 'BottomSalCorrected' : np.repeat(np.nan, len(preTms)), 'BottomSalBad' : np.repeat(True, len(preTms)), 'SurfaceTemp' : np.repeat(np.nan, len(preTms)),
         'BottomTemp' : np.repeat(np.nan, len(preTms)), 'BottomTempBad' : np.repeat(True, len(preTms)), 'BottomPressure' : np.repeat(np.nan, len(preTms))})
downDF = pd.concat([downDF, refillDF])
postTms = np.arange(lastMidMark, postTimestamp, datetime.timedelta(minutes = 5)).astype('datetime64')
refillDF = pd.DataFrame({'DN' : postTms, 'SurfaceSalCorrected' : np.repeat(np.nan, len(postTms)), 'BottomSalCorrected' : np.repeat(np.nan, len(postTms)), 'BottomSalBad' : np.repeat(True, len(postTms)), 'SurfaceTemp' : np.repeat(np.nan, len(postTms)),
         'BottomTemp' : np.repeat(np.nan, len(postTms)), 'BottomTempBad' : np.repeat(True, len(postTms)), 'BottomPressure' : np.repeat(np.nan, len(postTms))})
downDF = pd.concat([downDF, refillDF])
downDF = downDF.sort_values(['DN'], ascending = [True])

preTimestamp = pd.Timestamp('2013-10-24 22:05:00')
postTimestamp = pd.Timestamp('2014-03-12 19:30:00') + datetime.timedelta(minutes = 5)
firstMidMark = upDF['DN'][0]
lastMidMark = upDF['DN'][len(upDF['DN'])-1] + datetime.timedelta(minutes = 5)
preTms = np.arange(preTimestamp, firstMidMark, datetime.timedelta(minutes = 5)).astype('datetime64')
refillDF = pd.DataFrame({'DN' : preTms, 'SurfaceSalCorrected' : np.repeat(np.nan, len(preTms)), 'BottomSalCorrected' : np.repeat(np.nan, len(preTms)), 'BottomSalBad' : np.repeat(True, len(preTms)), 'SurfaceTemp' : np.repeat(np.nan, len(preTms)),
         'BottomTemp' : np.repeat(np.nan, len(preTms)), 'BottomTempBad' : np.repeat(True, len(preTms)), 'BottomPressure' : np.repeat(np.nan, len(preTms))})
upDF = pd.concat([upDF, refillDF])
postTms = np.arange(lastMidMark, postTimestamp, datetime.timedelta(minutes = 5)).astype('datetime64')
refillDF = pd.DataFrame({'DN' : postTms, 'SurfaceSalCorrected' : np.repeat(np.nan, len(postTms)), 'BottomSalCorrected' : np.repeat(np.nan, len(postTms)), 'BottomSalBad' : np.repeat(True, len(postTms)), 'SurfaceTemp' : np.repeat(np.nan, len(postTms)),
         'BottomTemp' : np.repeat(np.nan, len(postTms)), 'BottomTempBad' : np.repeat(True, len(postTms)), 'BottomPressure' : np.repeat(np.nan, len(postTms))})
upDF = pd.concat([upDF, refillDF])
upDF = upDF.sort_values(['DN'], ascending = [True])
'''
oceanTempDF = pd.merge_asof(downDF, combinedDF, left_on = 'DN', right_on = 'dayDN', direction = 'nearest')[["DN_x", "SurfaceTemp_y", "Temperature", "SurfaceSalCorrected_y", "Salinity", "dailyAverage", "AvgEstimatedTemp", "oceanSalEstimate"]]
oceanTempDF["AvgEstimatedTemp"] = oceanTempDF["AvgEstimatedTemp"].where(~oceanTempDF["AvgEstimatedTemp"].duplicated(), pd.NA)
oceanTempDF["oceanSalEstimate"] = oceanTempDF["oceanSalEstimate"].where(~oceanTempDF["oceanSalEstimate"].duplicated(), pd.NA)
oceanTempDF = oceanTempDF.interpolate()
riverTempDF = pd.merge_asof(downDF, riverCombinedDF, left_on = 'DN', right_on = 'dayDN', direction = 'nearest')[["DN_x","surfaceRiver", "bottomRiver", "EstimatedTemp"]]
riverTempDF = riverTempDF.rename(columns = {"DN_x": 'DN'})
riverTempDF["EstimatedTemp"] = riverTempDF["EstimatedTemp"].where(~riverTempDF["EstimatedTemp"].duplicated(), pd.NA)
riverTempDF = riverTempDF.interpolate()
oceanTempDF = oceanTempDF.rename(columns={"DN_x": "DN", "SurfaceTemp_y": "SurfaceTemp", "Temperature" : "MiniTemp", "SurfaceSalCorrected_y" : "SurfaceSalCorrected", "Salinity" : "MiniSal", "dailyAverage" : "Stonewall", "AvgEstimatedTemp" : "OceanTemp"})

#oceanTempDF.to_csv('ocean_temperature_interpol13_14.csv', index=False)
#riverTempDF.to_csv('river_temperature_interpol13_14.csv', index=False)

riverTempDF["riverSalinity"] = 0

tempFigLabels = ["surfaceRiver", "bottomRiver"]
tempfig = px.line(x = downDF['DN'], y = [riverTempDF["surfaceRiver"], riverTempDF["bottomRiver"]], color_discrete_sequence= ["black", "cyan"], title = "Temperature")
for idx in range(len(tempFigLabels)):
    tempfig.data[idx].name = tempFigLabels[idx]
    tempfig.data[idx].hovertemplate = 'variable=' + tempFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    tempfig.data[idx].legendgroup = tempFigLabels[idx]
tempfig.update_traces(patch={"line": {"dash": "dot"}}, selector={'name' : 'surfaceRiver'})
tempfig.update_traces(patch={"line": {"dash": "dot"}}, selector={'name' : 'bottomRiver'})

tempfig.add_scattergl(x= upDF['DN'], y = riverTempDF["EstimatedTemp"], line={'color': 'green', 'width' : 2}, name = "River Temperature")



tempfig.update_layout(title=dict(text= "Surface Temperature for 2013-2014", font=dict(size=25)))
tempfig.update_xaxes(tickangle=30)
tempfig.update_xaxes(rangeslider_visible=True)
tempfig.update_xaxes(range = [pd.Timestamp('2013-10-20'),pd.Timestamp('2014-03-15')])


tempfig.show()
